In [ ]:
import pandas as pd
import os

In [ ]:
os.getcwd()

In [ ]:
os.chdir('C:/Users/arsalan/UW/og_fhwa_kcm_transit_2021start - General/Analysis on ORCA data')

In [ ]:
ORCA_2023 = pd.read_csv('2023-04_orca_boardings.csv')

In [ ]:
ORCA_2023.head()

In [ ]:
pd.set_option('display.max_columns', None)
ORCA_2023

In [ ]:
ORCA_2023['card_id'].nunique()

In July, about 397,000 people rode King County Metro transit on an average weekday citywide, about 66,000 of them on BRT lines. More than 66,000 rode Sound Transit Express buses every day throughout their whole network, too. Trains, light rail, and streetcars made up 8 percent of commutes, the survey found (curbed.com, 2017).

In [ ]:
ORCA_2023['stop_code'].nunique()

In [ ]:
ORCA_2023['stop_id'].nunique()

Based on the analysis on the APC data it should be around 7000 bus stops in King County. Stop_id column has NAN values but is more accurate.

In [ ]:
ORCA_2023['device_id'].nunique()

In [ ]:
ORCA_2023['txn_id'].nunique()

In [ ]:
ORCA_2023['business_date'].nunique()

In [ ]:
# Group by 'card_id' and count unique 'stop_id' values within each group
bus_usage_count = ORCA_2023.groupby('card_id')['stop_code'].nunique()
# Create a new DataFrame to display the results
bus_usage_df = pd.DataFrame({'card_id': bus_usage_count.index, 'Number_of_stops_Used': bus_usage_count.values})

# Display the resulting DataFrame
print(bus_usage_df)

In this code:

We use the groupby method to group the DataFrame by the "card_id" column.
Then, we apply the nunique function to count the unique "stop_id" values within each group.
We create a new DataFrame (bus_usage_df) to display the results, with "card_id" and "Number_of_Buses_Used" as the column names.
Finally, we print the resulting DataFrame, which will show the number of buses each person used.
This code will give you a DataFrame where each row represents a unique "card_id" along with the corresponding number of buses used by that person.


In [ ]:
# Group by 'card_id' and count 'stop_id' values within each group
bus_stops_count = ORCA_2023.groupby('card_id')['stop_code'].count()

# Create a new DataFrame to display the results
bus_stops_df = pd.DataFrame({'card_id': bus_stops_count.index, 'Number_of_buses_Used': bus_stops_count.values})

# Display the resulting DataFrame
print(bus_stops_df)

In [ ]:
# Group by 'card_id' and 'business_date', then count unique 'stop_id' values within each group
unique_bus_stops_count = ORCA_2023.groupby(['card_id', 'business_date'])['stop_code'].nunique().reset_index()

# Rename the 'stop_id' column to 'Number_of_Unique_Stops_Used'
unique_bus_stops_count.rename(columns={'stop_code': 'Number_of_Unique_Stops_Used'}, inplace=True)

# Display the resulting DataFrame
print(unique_bus_stops_count)

In [ ]:
# Group by 'card_id' and 'business_date', then count 'stop_id' values within each group
bus_stops_count = ORCA_2023.groupby(['card_id', 'business_date'])['stop_code'].count().reset_index()

# Rename the 'stop_id' column to 'Number_of_Stops_Used'
bus_stops_count.rename(columns={'stop_code': 'Number_of_Stops_Used'}, inplace=True)

# Display the resulting DataFrame
print(bus_stops_count)

In [ ]:
# Group by 'card_id' and count unique 'business_date' values within each group
bus_days_count = ORCA_2023.groupby('card_id')['business_date'].nunique().reset_index()

# Rename the 'business_date' column to 'Number_of_Days_Used'
bus_days_count.rename(columns={'business_date': 'Number_of_Days_Used'}, inplace=True)

# Display the resulting DataFrame
print(bus_days_count)

In [ ]:
# Group by 'business_date' and calculate the sum of 'Number_of_Stops_Used' for each date
daily_stops_sum = bus_stops_count.groupby('card_id')['Number_of_Stops_Used'].sum().reset_index()

# Rename the 'Number_of_Stops_Used' column to 'Total_Stops_Used_Per_Day'
daily_stops_sum.rename(columns={'Number_of_Stops_Used': 'Total_Stops_Used_Per_Month'}, inplace=True)

# Display the resulting DataFrame with the total stops used per day
print(daily_stops_sum)

In [ ]:
# Merge the 'daily_stops_sum' DataFrame with 'bus_days_count' on 'card_id' using an inner join
merged_data = pd.merge(daily_stops_sum, bus_days_count, on='card_id', how='inner')

# Calculate the average number of bus stops in each month for each user
merged_data['Average_Stops_Per_Day_Per_Month'] = merged_data['Total_Stops_Used_Per_Month'] / merged_data['Number_of_Days_Used']

# Display the resulting DataFrame
print(merged_data[['card_id', 'Average_Stops_Per_Day_Per_Month']])

In [ ]:
# Group by 'card_id' and 'stop_id', then count the occurrences of each 'stop_id'
stop_usage_count = ORCA_2023.groupby(['card_id', 'stop_code']).size().reset_index(name='Stop_Frequency')

# Display the resulting DataFrame
print(stop_usage_count)

In [ ]:
# Calculate the total number of stops used for each card_id
total_stops_used = ORCA_2023.groupby('card_id')['stop_code'].count().reset_index()
total_stops_used.rename(columns={'stop_code': 'Total_Stops_Used'}, inplace=True)

# Merge the total stops used with the stop_usage_count DataFrame
stop_usage_count = pd.merge(stop_usage_count, total_stops_used, on='card_id')

# Display the resulting DataFrame
print(stop_usage_count)

In [ ]:
# Save the stop_usage_count DataFrame to a CSV file
stop_usage_count.to_csv('stop_usage_data.csv', index=False)

In [ ]:
total_stops_used = ORCA_2023.groupby('card_id')['stop_id'].nunique().reset_index()
total_stops_used.rename(columns={'stop_id': 'Total_Stops_Used_unique'}, inplace=True)

# Merge the total stops used with the stop_usage_count DataFrame
stop_usage_count = pd.merge(stop_usage_count, total_stops_used, on='card_id')

# Display the resulting DataFrame
print(stop_usage_count)

In [ ]:
# Save the stop_usage_count DataFrame to a CSV file
stop_usage_count.to_csv('stop_usage_data.csv', index=False)

CHANGING THE COORDINATION SYSTEM:

In [ ]:
import pandas as pd
import pyproj

In [ ]:
# Set the State Plane coordinate system for Washington State (EPSG:2926)
source_crs = pyproj.CRS.from_epsg(2926)

In [ ]:
# Set the target coordinate system to WGS84 (EPSG:4326)
target_crs = pyproj.CRS.from_epsg(4326)

In [ ]:
# Create a transformer to convert from source to target CRS
transformer = pyproj.Transformer.from_crs(source_crs, target_crs)

In [ ]:
# Apply the transformation to the coordinates in the data frame
ORCA_2023['Latitude'], ORCA_2023['Longitude'] = transformer.transform(ORCA_2023['device_lat'].values, ORCA_2023['device_lng'].values)

In [ ]:
ORCA_2023.to_csv("2023-04_orca_boardings_new_coordinates.csv", index=False)

The above projection did not work as it is not using the same coordinates as APC project. The values should just be devided by 1000000

In [ ]:
# Convert the 'device_lat' column to the desired format
ORCA_2023['device_lat'] = ORCA_2023['device_lat'] / 1000000
ORCA_2023['device_lng'] = ORCA_2023['device_lng'] / 1000000
# Display the DataFrame with the updated 'device_lat' values
print(ORCA_2023)

Adding locations to 'stop_usage_data.csv'

In [ ]:
# Merge the 'device_lat' and 'device_lng' columns from 'ORCA_2023' into 'stop_usage_count' by 'stop_id'
stop_usage_count_with_location = pd.merge(stop_usage_count, ORCA_2023[['stop_id', 'device_lat', 'device_lng']], on='stop_id', how='left')

# Display the resulting DataFrame
print(stop_usage_count_with_location)

In [ ]:
from sqlalchemy import create_engine

# Assuming 'stop_usage_count' and 'ORCA_2023' are your DataFrames

# Create a SQLite database and connect to it
db_engine = create_engine('sqlite:///mydatabase.db')

# Write DataFrames to the database
stop_usage_count.to_sql('stop_usage_count_table', db_engine, if_exists='replace', index=False)
ORCA_2023.to_sql('ORCA_2023_table', db_engine, if_exists='replace', index=False)

# Perform the merge in the database using SQL
query = """
SELECT a.*, b.device_lat, b.device_lng
FROM stop_usage_count_table AS a
LEFT JOIN ORCA_2023_table AS b
ON a.stop_id = b.stop_id;
"""

# Execute the SQL query and fetch the result into a DataFrame
merged_data = pd.read_sql_query(query, db_engine)

# Close the database connection
db_engine.dispose()

# Display the resulting DataFrame
print(merged_data)

In [1]:
!pip install folium
import folium
import pandas as pd
import datetime
from datetime import timedelta


In [2]:
df_23 = pd.read_csv('2023-04_orca_boardings.csv')

/var/folders/fh/zynvgz3502n7wqtzvnrpjnj40000gn/T/ipykernel_25433/342241639.py:1: DtypeWarning: Columns (17) have mixed types. Specify dtype option on import or set low_memory=False.
  df_23 = pd.read_csv('2023-04_orca_boardings.csv')


In [3]:
df_23 = df_23.sort_values(by=['business_date','card_id'], ascending=[True,True])

In [4]:
df_23

txn_id                boarding_guid  txn_type_id  card_id  \
256999   195660046   1536003r-70-46-6428623fc2e           66        2   
272054   195709760   155140d0-70-60-64287e453b8           66        4   
329901   195906358   1308607q-70-66-6428d2d5fce           66        4   
330115   195907290   1308607q-70-66-6428d2d5fce           84        4   
312589   195845680   165400a3-70-89-6428b977c22           66        9   
...            ...                          ...          ...      ...   
2420764  213969342   1627607s-70-62-644ec353bea           66  3577027   
2410688  213910784   13065018-70-43-644e904a1a2           66  3577863   
2415592  213938742   1286409v-70-38-644eabd0630           66  3577981   
5216060  214045842  1284301e-70-183-644ef8d330c           66  3577981   
2441357  214089128  1293809o-70-282-644f1a6e7c0           66  3578298   

         passenger_type_id  passenger_count  product_id business_date  \
256999                   1                1      1003.0    2023-04-01   
272054                   1                1      1003.0    2023-04-01   
329901                   1                1      1003.0    2023-04-01   
330115                   1                1      1003.0    2023-04-01   
312589                   1                1       102.0    2023-04-01   
...                    ...              ...         ...           ...   
2420764                  1                1         NaN    2023-04-30   
2410688                  1                1         NaN    2023-04-30   
2415592                  1                1         NaN    2023-04-30   
5216060                  1                1         NaN    2023-04-30   
2441357                  1                1         NaN    2023-04-30   

         device_id   device_dtm_pacific  ...  participant_group_id  \
256999     15360.0  2023-04-01 09:56:31  ...                1240.0   
272054     15514.0  2023-04-01 11:56:05  ...               29124.0   
329901     13086.0  2023-04-01 17:56:53  ...               29124.0   
330115     15704.0  2023-04-01 17:58:24  ...               29124.0   
312589     16540.0  2023-04-01 16:08:39  ...                   NaN   
...            ...                  ...  ...                   ...   
2420764    16276.0  2023-04-30 12:36:51  ...                   NaN   
2410688    13065.0  2023-04-30 08:59:06  ...                   NaN   
2415592    12864.0  2023-04-30 10:56:32  ...                   NaN   
5216060    12843.0  2023-04-30 16:25:07  ...                   NaN   
2441357    12938.0  2023-04-30 18:48:30  ...                   NaN   

            stop_id stop_code  ticket_internal_nbr  osfa_cents  ceffv_cents  \
256999   96403200.0     37040                  307         275          275   
272054   96408808.0     55583                  307         275          275   
329901   96440468.0     55778                  218         300          300   
330115   96408992.0     56031                  307         275          275   
312589   96400124.0      2672                  307         275          275   
...             ...       ...                  ...         ...          ...   
2420764  96409380.0       570                  307         275          275   
2410688  96440440.0      1108                  218         300          225   
2415592  96440504.0    990001                  218         325          325   
5216060  96440452.0       501                  218         300          300   
2441357  96440572.0     99903                  218         350          225   

         total_journey_fare_cents linked_journey_fare_cents  \
256999                        275                       275   
272054                        275                       275   
329901                        575                       300   
330115                        575                       300   
312589                        275                       275   
...                           ...                       ...   
2420764                    

In [5]:
df_23['device_lat'] = df_23['device_lat'] / 1000000
df_23['device_lng'] = df_23['device_lng'] / 1000000
df_23

txn_id                boarding_guid  txn_type_id  card_id  \
256999   195660046   1536003r-70-46-6428623fc2e           66        2   
272054   195709760   155140d0-70-60-64287e453b8           66        4   
329901   195906358   1308607q-70-66-6428d2d5fce           66        4   
330115   195907290   1308607q-70-66-6428d2d5fce           84        4   
312589   195845680   165400a3-70-89-6428b977c22           66        9   
...            ...                          ...          ...      ...   
2420764  213969342   1627607s-70-62-644ec353bea           66  3577027   
2410688  213910784   13065018-70-43-644e904a1a2           66  3577863   
2415592  213938742   1286409v-70-38-644eabd0630           66  3577981   
5216060  214045842  1284301e-70-183-644ef8d330c           66  3577981   
2441357  214089128  1293809o-70-282-644f1a6e7c0           66  3578298   

         passenger_type_id  passenger_count  product_id business_date  \
256999                   1                1      1003.0    2023-04-01   
272054                   1                1      1003.0    2023-04-01   
329901                   1                1      1003.0    2023-04-01   
330115                   1                1      1003.0    2023-04-01   
312589                   1                1       102.0    2023-04-01   
...                    ...              ...         ...           ...   
2420764                  1                1         NaN    2023-04-30   
2410688                  1                1         NaN    2023-04-30   
2415592                  1                1         NaN    2023-04-30   
5216060                  1                1         NaN    2023-04-30   
2441357                  1                1         NaN    2023-04-30   

         device_id   device_dtm_pacific  ...  participant_group_id  \
256999     15360.0  2023-04-01 09:56:31  ...                1240.0   
272054     15514.0  2023-04-01 11:56:05  ...               29124.0   
329901     13086.0  2023-04-01 17:56:53  ...               29124.0   
330115     15704.0  2023-04-01 17:58:24  ...               29124.0   
312589     16540.0  2023-04-01 16:08:39  ...                   NaN   
...            ...                  ...  ...                   ...   
2420764    16276.0  2023-04-30 12:36:51  ...                   NaN   
2410688    13065.0  2023-04-30 08:59:06  ...                   NaN   
2415592    12864.0  2023-04-30 10:56:32  ...                   NaN   
5216060    12843.0  2023-04-30 16:25:07  ...                   NaN   
2441357    12938.0  2023-04-30 18:48:30  ...                   NaN   

            stop_id stop_code  ticket_internal_nbr  osfa_cents  ceffv_cents  \
256999   96403200.0     37040                  307         275          275   
272054   96408808.0     55583                  307         275          275   
329901   96440468.0     55778                  218         300          300   
330115   96408992.0     56031                  307         275          275   
312589   96400124.0      2672                  307         275          275   
...             ...       ...                  ...         ...          ...   
2420764  96409380.0       570                  307         275          275   
2410688  96440440.0      1108                  218         300          225   
2415592  96440504.0    990001                  218         325          325   
5216060  96440452.0       501                  218         300          300   
2441357  96440572.0     99903                  218         350          225   

         total_journey_fare_cents linked_journey_fare_cents  \
256999                        275                       275   
272054                        275                       275   
329901                        575                       300   
330115                        575                       300   
312589                        275                       275   
...                           ...                       ...   
2420764                    

In [6]:
df_23['device_dtm_pacific'] = pd.to_datetime(df_23['device_dtm_pacific'])
df_23['business_date'] = pd.to_datetime(df_23['business_date'])
df_23['time_of_day'] = df_23['device_dtm_pacific'].dt.time

In [7]:
df_23=df_23[['card_id','business_date','time_of_day','device_lat','device_lng','stop_code','route_number']]

In [8]:
df_23

card_id business_date time_of_day  device_lat  device_lng stop_code  \
256999         2    2023-04-01    09:56:31   47.690703 -122.360021     37040   
272054         4    2023-04-01    11:56:05   47.523868 -122.278888     55583   
329901         4    2023-04-01    17:56:53   47.560280 -122.292892     55778   
330115         4    2023-04-01    17:58:24   47.560626 -122.293461     56031   
312589         9    2023-04-01    16:08:39   47.624075 -122.356790      2672   
...          ...           ...         ...         ...         ...       ...   
2420764  3577027    2023-04-30    12:36:51   47.608716 -122.336681       570   
2410688  3577863    2023-04-30    08:59:06   47.611450 -122.337532      1108   
2415592  3577981    2023-04-30    10:56:32   47.659875 -122.314194    990001   
5216060  3577981    2023-04-30    16:25:07   47.602139 -122.331055       501   
2441357  3578298    2023-04-30    18:48:30   47.445053 -122.296692     99903   

        route_number  
256999            45  
272054           106  
329901        100479  
330115           106  
312589           674  
...              ...  
2420764           40  
2410688       100479  
2415592       100479  
5216060       100479  
2441357       100479  

[5229140 rows x 7 columns]

In [9]:
df_23=df_23.dropna(subset=['stop_code'])

In [10]:
df_23.shape

(4994066, 7)

In [ ]:
lat=df_23.iloc[0]['device_lat']
lng=df_23.iloc[0]['device_lng']
num_rows = df_23.shape[0]
num_rows

In [ ]:
import random
def random_color():
    return "#{:02x}{:02x}{:02x}".format(random.randint(0, 200), random.randint(0, 200), random.randint(0, 200))


df_23 = df_23.dropna(subset=['device_lat','device_lng'])
num_rows = df_23.shape[0]
date = df_23.iloc[0]['business_date'].date()
card=1
lat=df_23.iloc[0]['device_lat']
lng=df_23.iloc[0]['device_lng']
m = folium.Map(location=[lat, lng], zoom_start=12)
# for i in range(204900,num_rows):
for i in range(num_rows):
    lat=df_23.iloc[i]['device_lat']
    lng=df_23.iloc[i]['device_lng']
    if(df_23.iloc[i]['business_date'].date()==date):
        if(df_23.iloc[i]['card_id']==card) and (i>0):
            folium.Marker([lat, lng], tooltip=f"Stop ID: {df_23.iloc[i]['stop_code']}").add_to(m)
            folium.Marker([df_23.iloc[i-1]['device_lat'], df_23.iloc[i-1]['device_lng']], tooltip=f"Stop ID: {df_23.iloc[i-1]['stop_code']}").add_to(m)
            line = folium.PolyLine(
                locations=[[lat, lng], [df_23.iloc[i-1]['device_lat'], df_23.iloc[i-1]['device_lng']]],
                color=co,
                weight=2,
                tooltip=f'Card ID: {card}'
            )
            line.add_to(m)
            m.save(f'map{date}.html')
            print(m)
        else:
            card=df_23.iloc[i]['card_id']
            co=random_color()
    else:
        date = date + timedelta(days=1)
        m = folium.Map(location=[lat, lng], zoom_start=12)



In [11]:
stop_usage_count


NameError: name 'stop_usage_count' is not defined

In [ ]:
stop_usage_count.to_csv('stop_usage_data.csv', index=False)

In [ ]:
date

In [12]:
df_232=df_23.sort_values(by=['card_id','business_date'], ascending=[True,True])

Extracting Origin and destinations:

In [11]:
trip_count = df_23.groupby('card_id')['business_date'].value_counts().reset_index(name='trip_count')

In [12]:
trip_count

card_id business_date  trip_count
0              1    2023-04-02           2
1              1    2023-04-04           2
2              1    2023-04-18           2
3              1    2023-04-20           2
4              1    2023-04-24           2
...          ...           ...         ...
2187773  3577246    2023-04-29           3
2187774  3577863    2023-04-30           1
2187775  3577981    2023-04-30           2
2187776  3578120    2023-04-29           1
2187777  3578298    2023-04-30           1

[2187778 rows x 3 columns]

In [13]:
count_of_ones = (trip_count['trip_count'] == 1).sum()
print(count_of_ones)
count_of_non_ones = (trip_count['trip_count'] != 1).sum()
count_of_ones/(count_of_ones+count_of_non_ones)*100

656816


30.022058910913263

In [ ]:
origin_data = df_23[df_23['time_of_day']>=pd.to_datetime('04:00:00', format='%H:%M:%S').time()].groupby(['card_id', 'business_date'])['stop_code'].first().reset_index()
origin_data=origin_data.rename(columns={"stop_code":"first origin (home)"})

In [14]:
df_23.shape

(4994066, 7)

In [ ]:
df_23[(df_23['time_of_day']<=pd.to_datetime('05:00:00', format='%H:%M:%S').time()) & (df_23['time_of_day']>=pd.to_datetime('04:00:00', format='%H:%M:%S').time())]

In [ ]:
df_23[(df_23['time_of_day']<=pd.to_datetime('04:00:00', format='%H:%M:%S').time()) & (df_23['time_of_day']>=pd.to_datetime('03:00:00', format='%H:%M:%S').time())]

In [ ]:
origin_data

In [15]:
df_23=df_23.sort_values(by=['card_id','business_date','time_of_day'], ascending=[True,True,True])

In [16]:
nan_exists = df_23[['card_id', 'business_date', 'time_of_day']].isna().any()
print(nan_exists)

card_id          False
business_date    False
time_of_day      False
dtype: bool


In [ ]:
taz={}

card_id=df_23['card_id'].unique().tolist()
n_card_id=df_23['card_id'].nunique()
dates=df_23.groupby(['card_id'])['business_date'].unique().to_dict()
#times=df_23.groupby(['card_id','business_date'])['time_of_day'].unique()
#n_date=df_23.groupby(['card_id'])['business_date'].nunique()
#print(n_date[n_date.index==2].iloc[0])
print(dates[4])
#print(times[times.index==4,'00:00:00'])

#for i in range(len(df_23)):


In [17]:
print(df_23.shape)
all_numeric = pd.to_numeric(df_23['stop_code'], errors='coerce').notna().all()

if all_numeric:
    print("All values in 'stop_code' are numbers.")
else:
    print("Not all values in 'stop_code' are numbers.")

df_23 = df_23[pd.to_numeric(df_23['stop_code'], errors='coerce').notna()]
print(df_23.shape)

(4994066, 7)
Not all values in 'stop_code' are numbers.
(4853394, 7)


In [17]:
am4=pd.to_datetime('04:00:00', format='%H:%M:%S').time()
am0=pd.to_datetime('00:00:00', format='%H:%M:%S').time()

df_23[(df_23['time_of_day']<am4) & (df_23['time_of_day']>am0)]


In [ ]:
df_23[df_23['card_id']==74]

In [ ]:
df_23[df_23['card_id']==1]


In [ ]:
df_23[df_23['card_id']==2]

In [18]:
import warnings
warnings.filterwarnings("ignore")
import json
import numpy as np

In [51]:
taz={}
am4=pd.to_datetime('04:00:00', format='%H:%M:%S').time()
am0=pd.to_datetime('00:00:00', format='%H:%M:%S').time()

for person in card_id:
    for index in range(len(dates[person])):
        d=dates[person][index]
        df = df_23[(df_23['card_id'] == person) & (df_23['business_date'] == d)].reset_index()
        df=df[df['time_of_day'] >= am4]
        if index < len(dates[person]) - 1:
            dd = dates[person][index + 1]
            dff = df_23[(df_23['card_id'] == person) & (df_23['business_date'] == dd)].reset_index()
            dff = dff[(dff['time_of_day'] < am4) & (dff['time_of_day'] >= am0)]
            df = df.append(dff, ignore_index=True)
            df = df.reset_index(drop=True)
        n = df.shape[0]
        if (n==1 or n==0): continue
        origin = df['stop_code'].iloc[0]
        o = origin
        # idx= df.loc[df['time_of_day'] >= am4, 'stop_code'].index[0]
        for i in range(n-1):
            taz.setdefault(o, [])
            tod = df['time_of_day'][i]
            time_diff = datetime.datetime.combine(df['business_date'][i+1].date(), df['time_of_day'][i+1]) - datetime.datetime.combine(df['business_date'][i].date(),df['time_of_day'][i])
            if time_diff.total_seconds() > 7200 or i+1==n-1:
                destination=df['stop_code'][i+1]
                taz.setdefault(destination, [])
                taz[o].append(destination)
                o=destination
                if (i+1==n-1): taz[destination].append(origin)
    print(person)
    # max_length = max(len(v) for v in taz.values())
    # for key in taz:
    #     taz[key] += [None] * (max_length - len(taz[key]))
    # output = pd.DataFrame(taz)
    # output.to_excel('output.csv', index=False)
    with open('output.json', "w") as json_file:
         json.dump(taz, json_file, indent=4)

# output = pd.DataFrame(taz)
# output.to_csv('output.csv', index=False)






In [ ]:
taz={}
am4=pd.to_datetime('04:00:00', format='%H:%M:%S').time()
am0=pd.to_datetime('00:00:00', format='%H:%M:%S').time()

for person in card_id:
    for index in range(len(dates[person])):
        d=dates[person][index]
        df = df_23[(df_23['card_id'] == person) & (df_23['business_date'] == d)].reset_index()
        df=df[df['time_of_day'] >= am4]
        if index < len(dates[person]) - 1: # you should add this later
            dd = dates[person][index + 1]
            dff = df_23[(df_23['card_id'] == person) & (df_23['business_date'] == dd)].reset_index()
            dff = dff[(dff['time_of_day'] < am4) & (dff['time_of_day'] >= am0)]
            df = df.append(dff, ignore_index=True)
        df = df.reset_index(drop=True)
        n = df.shape[0]
        if (n==1 or n==0): continue
        origin = df['stop_code'].iloc[0]
        o = origin
        # idx= df.loc[df['time_of_day'] >= am4, 'stop_code'].index[0]
        for i in range(n-1):
            taz.setdefault(o, [])
            # tod = df['time_of_day'][i]
            time_diff = datetime.datetime.combine(df['business_date'][i+1].date(), df['time_of_day'][i+1]) - datetime.datetime.combine(df['business_date'][i].date(),df['time_of_day'][i])
            if time_diff.total_seconds() > 7200 or i+1==n-1:
                destination=df['stop_code'][i+1]
                taz.setdefault(destination, [])
                taz[o].append(destination)
                o=destination
                if (i+1==n-1): taz[destination].append(origin)
    print(person)
    # max_length = max(len(v) for v in taz.values())
    # for key in taz:
    #     taz[key] += [None] * (max_length - len(taz[key]))
    # output = pd.DataFrame(taz)
    # output.to_excel('output.csv', index=False)
    with open('output.json', "w") as json_file:
         json.dump(taz, json_file, indent=4)

# output = pd.DataFrame(taz)
# output.to_csv('output.csv', index=False)






In [19]:
df_23

card_id business_date time_of_day  device_lat  device_lng stop_code  \
439379         1    2023-04-02    19:24:54   47.611710 -122.324195      3034   
447746         1    2023-04-02    22:44:02   47.626855 -122.356853      2680   
679314         1    2023-04-03    23:54:55   47.611960 -122.335771      1110   
801361         1    2023-04-04    14:09:12   47.701158 -122.355461      5730   
809699         1    2023-04-04    14:46:02   47.609986 -122.337038      1180   
...          ...           ...         ...         ...         ...       ...   
2410688  3577863    2023-04-30    08:59:06   47.611450 -122.337532      1108   
2415592  3577981    2023-04-30    10:56:32   47.659875 -122.314194    990001   
5216060  3577981    2023-04-30    16:25:07   47.602139 -122.331055       501   
5187245  3578120    2023-04-29    21:50:46   47.809686 -122.382485      2727   
2441357  3578298    2023-04-30    18:48:30   47.445053 -122.296692     99903   

        route_number  
439379             2  
447746             2  
679314            11  
801361             5  
809699            10  
...              ...  
2410688       100479  
2415592       100479  
5216060       100479  
5187245          196  
2441357       100479  

[4853394 rows x 7 columns]

In [49]:
taz={}
am4=pd.to_datetime('04:00:00', format='%H:%M:%S').time()
am0=pd.to_datetime('00:00:00', format='%H:%M:%S').time()


# def custom_investigation(group):
#     n=len(group['time_of_day'])
#     origin=group['stop_code'].first()
#     for i in range(n-1):
#         time_diff = datetime.strptime(group['time_of_day'].iloc[i+1], '%H:%M:%S') - \
#                     datetime.strptime(group['time_of_day'].iloc[i], '%H:%M:%S')
#         if time_diff.total_seconds() > 7200 or i+1==n-1:
#             group['destination'].iloc[i]=group['stop_code'].iloc[i+1]
#             group['origin'].iloc[i]=group['stop_code'].iloc[i]
#             if (i+1==n-1):
#                 group['origin'].iloc[i+1]=group['stop_code'].iloc[i+1]
#                 group['destination'].iloc[i+1]=origin
#         else:
#             group['origin'].iloc[i]=group['stop_code'].iloc[i]
#             #what about the trip after transfer? this way the origin for that trip would consider transfer stop
#    return pd.Series({'Origin': mean_value, 'Destination': max_value})

def custom_investigation(group):
    n=len(group['time_of_day'])
    origin=group['stop_code'].iloc[0]
    o = origin
    for i in range(n-1):
        taz.setdefault(o, [])
        time_diff = datetime.datetime.combine(group['business_date'].iloc[i+1].date(), group['time_of_day'].iloc[i+1]) - datetime.datetime.combine(group['business_date'].iloc[i].date(),group['time_of_day'].iloc[i])
        if time_diff.total_seconds() > 7200 or i+1==n-1:
            destination=group['stop_code'].iloc[i+1]
            taz.setdefault(destination, [])
            taz[o].append(destination)
            o=destination
            if (i+1==n-1): taz[destination].append(origin)


    return taz

result = df_23.groupby(['card_id', 'business_date']).apply(custom_investigation)

# tazdf = pd.DataFrame(taz.items())
# tazdf.to_excel('tazs.xlsx', index=False)

with open('output.json', "w") as json_file:
     json.dump(taz, json_file, indent=4)

['2680', '570', '450', '22820', '468', '2672', '2670', '600', '575', '575', '13721', '600', '79520', '60428', '605', '1480', '2672', '2672', '558', '400', '400', '400', '400', '400', '400', '400', '19940', '17310', '455', '455', '1651', '430', '2875', '2680', '2180', '420', '420', '1580', '1580', '1580', '1270', '1580', '1270', '450', '1270', '1270', '1580', '29270', '33220', '468', '11175', '430', '18270', '420', '1471', '468', '32371', '468', '11175', '13460', '1230', '1215', '455', '67019', '67019', '455', '2672', '55578', '67014', '1230', '455', '16430', '3034', '16407', '2672', '641', '641', '1590', '641', '641', '641', '2245', '26645', '26645', '558', '558', '6176', '6176', '26645', '18359', '31731', '6176', '420', '450', '420', '420', '400', '420', '420', '420', '420', '67019', '67019', '67019', '67019', '1270', '19790', '19790', '468', '19750', '19790', '2672', '2180', '1270', '1230', '1230', '1230', '1215', '1215', '1215', '1230', '1230', '1230', '1230', '420', '39431', '450',

In [20]:
with open('output.json', 'r') as json_file:
    taz = json.load(json_file)

In [21]:
taz

{'3034': ['2680',
  '570',
  '450',
  '22820',
  '468',
  '2672',
  '2670',
  '600',
  '575',
  '575',
  '13721',
  '600',
  '79520',
  '60428',
  '605',
  '1480',
  '2672',
  '2672',
  '558',
  '400',
  '400',
  '400',
  '400',
  '400',
  '400',
  '400',
  '19940',
  '17310',
  '455',
  '455',
  '1651',
  '430',
  '2875',
  '2680',
  '2180',
  '420',
  '420',
  '1580',
  '1580',
  '1580',
  '1270',
  '1580',
  '1270',
  '450',
  '1270',
  '1270',
  '1580',
  '29270',
  '33220',
  '468',
  '11175',
  '430',
  '18270',
  '420',
  '1471',
  '468',
  '32371',
  '468',
  '11175',
  '13460',
  '1230',
  '1215',
  '455',
  '67019',
  '67019',
  '455',
  '2672',
  '55578',
  '67014',
  '1230',
  '455',
  '16430',
  '3034',
  '16407',
  '2672',
  '641',
  '641',
  '1590',
  '641',
  '641',
  '641',
  '2245',
  '26645',
  '26645',
  '558',
  '558',
  '6176',
  '6176',
  '26645',
  '18359',
  '31731',
  '6176',
  '420',
  '450',
  '420',
  '420',
  '400',
  '420',
  '420',
  '420',
  '420',
  '6

In [22]:
len(taz)

8863

In [25]:
print(df_23['stop_code'].nunique())

9043


In [29]:
len(taz['3036'])

1109

In [30]:
a=0
for key, values in taz.items():
    for value in values:
        a+=1
print(a)

3385806


Flow analysis:
First, I want to exclude passengers who only used one bus stop (unique) in a month. They might have more than one bus stop usage but if all of them are from one bus stop it will not be useful so we filter them

In [ ]:
# Count the number of times each card_id used the bus
usage_counts = ORCA_2023.groupby('card_id')['stop_code'].nunique()
print(ORCA_2023[ORCA_2023.card_id==84])

# Identify card_ids that used the bus only once
card_ids_to_exclude = usage_counts[usage_counts == 1].index
print(usage_counts[usage_counts == 0])
# Exclude card_ids with usage count 1 from the original dataset
filtered_data = ORCA_2023[~ORCA_2023['card_id'].isin(card_ids_to_exclude)]

In [ ]:
print(card_ids_to_exclude.shape)
print(ORCA_2023.shape)
print(filtered_data.shape)

In [ ]:
# Count the number of times each card_id used the bus
usage_counts = ORCA_2023.groupby('card_id')['stop_code'].count()
print(usage_counts)
# Identify card_ids that used the bus only once
card_ids_to_exclude = usage_counts[usage_counts == 0].index
print(card_ids_to_exclude.shape)

We also have zeros in stop counts (I don't know why). So, I exported usage counts data to excel.

In [ ]:
usage_counts = ORCA_2023.groupby('card_id')['stop_code'].count()

# Convert the usage_counts to a DataFrame for easier export to Excel
usage_counts_df = pd.DataFrame({'card_id': usage_counts.index, 'usage_count': usage_counts.values})

# Specify the file path including the directory
excel_file_path = './usage_counts.xlsx'

# Export to Excel
usage_counts_df.to_excel(excel_file_path, index=False, sheet_name='UsageCounts')


I want to exclude zeros now:

In [ ]:
# Count the number of times each card_id used the bus
usage_counts = ORCA_2023.groupby('card_id')['stop_code'].count()
print(usage_counts)
# Identify card_ids that used the bus only once
card_ids_to_exclude = usage_counts[usage_counts == 0].index
print(card_ids_to_exclude.shape)
# Exclude card_ids with usage count 1 from the original dataset
filtered_data = filtered_data[~filtered_data['card_id'].isin(card_ids_to_exclude)]

In [ ]:
filtered_data

In [ ]:
# Count the number of times each card_id used the bus in each day
usage_counts = ORCA_2023.groupby(['card_id', 'business_date'])['stop_code'].count().reset_index()

# Identify card_ids that used the bus only once
card_ids_to_exclude = usage_counts[usage_counts == 0].index
card_ids_to_exclude.shape

In [ ]:
Assigning origins

In [ ]:
# Count the number of times each card_id used the bus in each day
usage_counts = ORCA_2023.groupby(['card_id', 'business_date'])['stop_code'].count().reset_index()

# Identify card_ids that used the bus only once
card_ids_to_exclude = usage_counts[usage_counts == 2].index
card_ids_to_exclude.shape

In [ ]:
filtered_data['device_dtm_pacific'] = pd.to_datetime(filtered_data['device_dtm_pacific'])
filtered_data['device_time'] = filtered_data['device_dtm_pacific'].dt.time

# Group by 'card_id', 'business_day', and 'txn_id' to identify the first trip (earliest time)
first_trip = filtered_data.groupby(['card_id', 'business_date', 'txn_id'], as_index=False)['device_time'].min()

# Extract the first stop_id as origin for each 'card_id' on each 'business_day'
origin_data = filtered_data.groupby(['card_id', 'business_date'])['stop_id'].first().reset_index()

# Print the data with origins
print(origin_data)

In [ ]:
filtered_data